In [1]:
import csv
import community
import pandas as pd
import networkx as nx
import math
import matplotlib.pyplot as plt
import pickle
import requests
import xml.etree.ElementTree as ET
from bs4 import BeautifulSoup
import re

In [2]:
#http://api.openaire.eu/search/publications
#resp = requests.get('http://api.openaire.eu/search/publications?size=100&hasProject=yes')
#http://api.openaire.eu/oai_pmh?verb=ListRecords&set=projects&metadataPrefix=oaf&resumptionToken=
#
resp = requests.get('https://zenodo.org/oai2d?verb=ListRecords&set=user-ecfunded&metadataPrefix=oai_dc')
resp.content

'<?xml version=\'1.0\' encoding=\'UTF-8\'?>\n<?xml-stylesheet type="text/xsl" href="/static/xsl/oai2.xsl"?>\n<OAI-PMH xmlns="http://www.openarchives.org/OAI/2.0/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.openarchives.org/OAI/2.0/ http://www.openarchives.org/OAI/2.0/OAI-PMH.xsd">\n  <responseDate>2018-11-23T15:35:50Z</responseDate>\n  <request verb="ListRecords" set="user-ecfunded" metadataPrefix="oai_dc">https://zenodo.org/oai2d</request>\n  <ListRecords>\n    <record>\n      <header>\n        <identifier>oai:zenodo.org:814224</identifier>\n        <datestamp>2018-04-10T11:35:13Z</datestamp>\n        <setSpec>openaire_data</setSpec>\n        <setSpec>user-lanka</setSpec>\n        <setSpec>user-ecfunded</setSpec>\n      </header>\n      <metadata>\n        <oai_dc:dc xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:oai_dc="http://www.openarchives.org/OAI/2.0/oai_dc/" xsi:schemaLocation="http://www.openarchives.org/OAI/2.0/oai_dc/ http://www.o

In [3]:
soup = BeautifulSoup(resp.content, 'lxml')
soup.prettify()

u'<?xml version=\'1.0\' encoding=\'UTF-8\'?>\n<?xml-stylesheet type="text/xsl" href="/static/xsl/oai2.xsl"?>\n<html>\n <body>\n  <oai-pmh xmlns="http://www.openarchives.org/OAI/2.0/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemalocation="http://www.openarchives.org/OAI/2.0/ http://www.openarchives.org/OAI/2.0/OAI-PMH.xsd">\n   <responsedate>\n    2018-11-23T15:35:50Z\n   </responsedate>\n   <request metadataprefix="oai_dc" set="user-ecfunded" verb="ListRecords">\n    https://zenodo.org/oai2d\n   </request>\n   <listrecords>\n    <record>\n     <header>\n      <identifier>\n       oai:zenodo.org:814224\n      </identifier>\n      <datestamp>\n       2018-04-10T11:35:13Z\n      </datestamp>\n      <setspec>\n       openaire_data\n      </setspec>\n      <setspec>\n       user-lanka\n      </setspec>\n      <setspec>\n       user-ecfunded\n      </setspec>\n     </header>\n     <metadata>\n      <oai_dc:dc xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:oai_dc="http:/

In [19]:
#retrieve projects from openaire
#build a 2d list in the form of grantID - date
#get first request
resptwo = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&set=projects&metadataPrefix=oaf')
#NOTE: size is set to 1000 by default
#TODO: retrieve resumption token, put in loop
souptwo = BeautifulSoup(resptwo.content, 'lxml')
#http://api.openaire.eu/oai_pmh?verb=ListRecords&set=projects&metadataPrefix=oaf
souptwo

<?xml version="1.0" encoding="UTF-8"?><html><body><oai:oai-pmh xmlns:oai="http://www.openarchives.org/OAI/2.0/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemalocation="http://www.openarchives.org/OAI/2.0/\n         http://www.openarchives.org/OAI/2.0/OAI-PMH.xsd">\n<oai:responsedate>2018-11-23T15:51:00Z</oai:responsedate>\n<oai:request metadataprefix="oaf" set="projects" verb="ListRecords">http://api.openaire.eu/oai_pmh</oai:request>\n<oai:listrecords>\n<oai:record>\n<oai:header>\n<oai:identifier>oai:dnet:arc_________::00cf0ad69cca348f1f9a15d343b31fa2</oai:identifier>\n<oai:datestamp>2018-08-07T00:00:00Z</oai:datestamp>\n<oai:setspec>Australian_Research_Council__ARC__-_Grants_Registry</oai:setspec>\n<oai:setspec>projects</oai:setspec>\n</oai:header>\n<oai:metadata>\n<oaf:entity xmlns:oaf="http://namespace.openaire.eu/oaf" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemalocation="http://namespace.openaire.eu/oaf https://www.openaire.eu/schema/1.0/oaf-1.

In [45]:
#takes resumption token string as an input, returns part before the first separator
def getMaxRecords(totalstring):
    splitted = totalstring.split('|')
    #print splitted[0]
    #result = str(splitted[len(splitted)-2])
    return splitted[0];

In [47]:
#takes resumption token string as an input, returns part before the first separator
def getCurrentRecords(totalstring):
    splitted = totalstring.split('|')
    #print splitted[0]
    #result = str(splitted[len(splitted)-2])
    return splitted[3];

In [53]:
#transform resumption token into appropriate string: https://www.openarchives.org/OAI/openarchivesprotocol.html#HTTPRequestFormat
def getGoodToken(totalstring):
    result = totalstring.replace(' ', '%20')
    return result;

In [48]:
getCurrentRecords(u'2544493|oaf|* AND oaftype exact "project"|2000|5beebb23be047061a7690bc3|false|projects')

u'2000'

In [54]:
getGoodToken(u'2544493|oaf|* AND oaftype exact "project"|2000|5beebb23be047061a7690bc3|false|projects')

u'2544493|oaf|*%20AND%20oaftype%20exact%20"project"|2000|5beebb23be047061a7690bc3|false|projects'

In [60]:
#while page < max, use resumptiontokens to extract soups, then put all data into one big soup?
#resptwo = requests.get('http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=2544493|oaf|*%20AND%20oaftype%20exact%20"project"|1000|5beebb231e82123b9ba6b95d|false|projects')
#get resumptiontoken
soups = list()
restoken = souptwo.find(re.compile("^oai:resumptiontoken"))
maxrecords = getMaxRecords(restoken.text)
currecords = getCurrentRecords(restoken.text)
#while currecords < maxrecords:
for i in range(2000, 2544493, 1000):
    print currecords,"/",maxrecords
    newtoken = getGoodToken(restoken.text)
    requestring = 'http://api.openaire.eu/oai_pmh?verb=ListRecords&resumptionToken=' + newtoken
    resploop = requests.get(requestring)
    souploop = BeautifulSoup(resploop.content, 'lxml')
    soups.append(souploop)
    restoken = souploop.find(re.compile("^oai:resumptiontoken"))
    #extract max and currently shown records
    maxrecords = getMaxRecords(restoken.text)
    currecords = getCurrentRecords(restoken.text)
    #print currecords,"/",maxrecords

2000 / 2544493
3000 / 2544493
4000 / 2544493
5000 / 2544493
6000 / 2544493


KeyboardInterrupt: 

In [56]:
temp = '2544493|oaf|* AND oaftype exact "project"|1000|5beebb231e82123b9ba6b95d|false|projects'
       '2544493|oaf|* AND oaftype exact "project"|1000|5beebb231e82123b9ba6b95d|false|projects'
newtemp = temp.replace(' ', '%20')
newtemp

IndentationError: unexpected indent (<ipython-input-56-8d022637353c>, line 2)

In [23]:
#get list of project codes
recordstwo=souptwo.find_all('code')

In [24]:
#for each record
    #find siblings with date
    #put record + date into grantdict
grantdict = dict()
for record in recordstwo:
    for sibling in record.previous_siblings:
        if sibling.name == 'startdate':
            recorddate = sibling.text #need to parse the date
    #grantlist.append([record.text, recorddate])
    grantdict[record.text] = recorddate
    #print "record", record.text
grantdict

{u'125270': u'2017-01-01',
 u'295068': u'2012-05-01',
 u'DP130102433': u'2017-05-01',
 u'632657': u'2017-01-01',
 u'P 21101': u'2017-01-01',
 u'5R01DC001262-22': u'1991-07-01',
 u'1046037': u'2017-01-01',
 u'DP0772223': u'2017-05-01',
 u'DE120100992': u'2008-06-01',
 u'1104528': u'2016-01-01',
 u'246193': u'2008-06-01',
 u'SFRH/BDE/51542/2011': u'2017-01-01',
 u'205693': u'2017-05-01',
 u'675530': u'2017-01-01',
 u'LP0776651': u'2017-05-01',
 u'980652': u'1998-01-01',
 u'36663': u'2017-01-01',
 u'1R01DA019217-01': u'2004-09-30',
 u'1R01HL073471-01A1': u'2003-12-15',
 u'1120615': u'2017-01-01',
 u'711265': u'2017-01-01',
 u'226195': u'2008-06-01',
 u'5R21DE016361-02': u'2004-09-28',
 u'82449': u'2017-01-01',
 u'626897': u'2015-02-01',
 u'DE180100112': u'2018-01-01',
 u'N01AI062532-007': u'1986-07-01',
 u'1R03HD047768-01': u'2004-07-01',
 u'737802': u'2016-12-01',
 u'254139': u'2010-06-01',
 u'1521': u'2017-01-01',
 u'DP180100966': u'2008-06-01',
 u'SFRH/BD/23030/2005': u'2017-01-01',
 u

In [25]:
#get a list of all objects with ID and http links (the other ones are repeating - e.g. oai)
#records=soup.find_all(re.compile("^dc:identifier"), string=re.compile("http"))
records=soup.find_all(re.compile("^dc:identifier"))

In [27]:
#clean records - leave only doi identifiers
#WHY this needs two times execution?
for record in records:
    if ("http" in record.text) or ("oai:" in record.text):
        records.remove(record)
        print record.text,' removed'
records

https://zenodo.org/record/1068107  removed
https://zenodo.org/record/229864  removed
https://zenodo.org/record/208217  removed
https://zenodo.org/record/835019  removed
https://zenodo.org/record/221384  removed
https://zenodo.org/record/54535  removed
https://zenodo.org/record/1202318  removed
https://zenodo.org/record/838173  removed
https://zenodo.org/record/260254  removed
https://zenodo.org/record/1202365  removed
https://zenodo.org/record/1157992  removed
https://zenodo.org/record/236182  removed
https://zenodo.org/record/1158728  removed
https://zenodo.org/record/1181908  removed
https://zenodo.org/record/1120292  removed
https://zenodo.org/record/834959  removed
https://zenodo.org/record/1210120  removed
https://zenodo.org/record/1210122  removed
https://zenodo.org/record/1187045  removed
https://zenodo.org/record/259382  removed
https://zenodo.org/record/240501  removed
https://zenodo.org/record/1134437  removed
https://zenodo.org/record/1186805  removed
https://zenodo.org/reco

[<dc:identifier>10.5281/zenodo.814224</dc:identifier>,
 <dc:identifier>10.1080/19440049.2017.1310396</dc:identifier>,
 <dc:identifier>10.5281/zenodo.229864</dc:identifier>,
 <dc:identifier>10.5281/zenodo.208217</dc:identifier>,
 <dc:identifier>10.5281/zenodo.835019</dc:identifier>,
 <dc:identifier>10.1038/srep39043</dc:identifier>,
 <dc:identifier>10.5281/zenodo.54535</dc:identifier>,
 <dc:identifier>10.5281/zenodo.1202318</dc:identifier>,
 <dc:identifier>10.1080/10286632.2017.1343309</dc:identifier>,
 <dc:identifier>10.1109/ASMS-SPSC.2014.6934521</dc:identifier>,
 <dc:identifier>10.5281/zenodo.1202365</dc:identifier>,
 <dc:identifier>10.5281/zenodo.1157992</dc:identifier>,
 <dc:identifier>10.5281/zenodo.236182</dc:identifier>,
 <dc:identifier>10.1007/978-3-319-34208-5</dc:identifier>,
 <dc:identifier>10.1016/j.neubiorev.2017.06.015</dc:identifier>,
 <dc:identifier>10.1080/17441692.2017.1371203</dc:identifier>,
 <dc:identifier>10.5281/zenodo.834959</dc:identifier>,
 <dc:identifier>10.5

In [28]:
#for each object ID
    #add that object ID to the nodelist
    #find siblings with tag "dc:relation" and add them to the nodelist
    #create edge between relation and object ID nodes, add edge to edgelist
nodelist = list()
edgelist = list()
for record in records:
    for sibling in record.previous_siblings:
        if sibling.name == 'dc:date':
            recorddate = sibling.text #need to parse the date
    nodelist.append([record.text, recorddate])
    #print "record", record.text
    for sibling in record.next_siblings:
        if sibling.name == 'dc:relation':
            if 'grantAgreement' in sibling.text:
                print sibling.text
                projectcode = str(getProjectCode(sibling.text)).strip()
                print projectcode
                if projectcode in grantdict:
                    grantdate = grantdict[str(projectcode)]
                    print grantdate
                else:
                    print projectcode,"not found in grant dictionary"
            nodelist.append(sibling.text)
            #print "relation", sibling.text
            edgelist.append([record.text, sibling.text])
#edgelist
#nodelist

info:eu-repo/grantAgreement/EC/FP7/609823/
609823
609823 not found in grant dictionary
info:eu-repo/grantAgreement/EC/H2020/734164/
734164
734164 not found in grant dictionary
info:eu-repo/grantAgreement/EC/H2020/654237/
654237
654237 not found in grant dictionary
info:eu-repo/grantAgreement/EC/H2020/687902/
687902
687902 not found in grant dictionary
info:eu-repo/grantAgreement/EC/FP7/294935/
294935
294935 not found in grant dictionary
info:eu-repo/grantAgreement/EC/FP7/267583/
267583
267583 not found in grant dictionary
info:eu-repo/grantAgreement/SNSF/Project+funding/100015_138331/
100015_138331
100015_138331 not found in grant dictionary
info:eu-repo/grantAgreement/EC/H2020/693799/
693799
693799 not found in grant dictionary
info:eu-repo/grantAgreement/EC/FP7/318306/
318306
318306 not found in grant dictionary
info:eu-repo/grantAgreement/SNSF/Project+funding/100015_138331/
100015_138331
100015_138331 not found in grant dictionary
info:eu-repo/grantAgreement/EC/H2020/689669/
689669


In [14]:
#takes EC projectID line as an input, returns only the 6 digit EC project code
def getProjectCode(totalstring):
    splitted = totalstring.split('/')
    result = str(splitted[len(splitted)-2])
    return result;

In [15]:
getProjectCode('info:eu-repo/grantAgreement/EC/FP7/603264/')

'603264'

In [16]:
grantdict['248919']

KeyError: '248919'

In [17]:
root = ET.fromstring(resp.content)

In [153]:
print(root.findall('.//*'))

[<Element '{http://www.openarchives.org/OAI/2.0/}responseDate' at 0x14460210>, <Element '{http://www.openarchives.org/OAI/2.0/}request' at 0x14460cd0>, <Element '{http://www.openarchives.org/OAI/2.0/}ListRecords' at 0x14460df0>, <Element '{http://www.openarchives.org/OAI/2.0/}record' at 0xdec5db0>, <Element '{http://www.openarchives.org/OAI/2.0/}header' at 0xdec5a10>, <Element '{http://www.openarchives.org/OAI/2.0/}identifier' at 0xdec56f0>, <Element '{http://www.openarchives.org/OAI/2.0/}datestamp' at 0xdec5d30>, <Element '{http://www.openarchives.org/OAI/2.0/}setSpec' at 0xdec5ab0>, <Element '{http://www.openarchives.org/OAI/2.0/}setSpec' at 0xdec52d0>, <Element '{http://www.openarchives.org/OAI/2.0/}setSpec' at 0xdec5970>, <Element '{http://www.openarchives.org/OAI/2.0/}metadata' at 0xdec5e50>, <Element '{http://www.openarchives.org/OAI/2.0/oai_dc/}dc' at 0xdec5d90>, <Element '{http://purl.org/dc/elements/1.1/}creator' at 0xdec5eb0>, <Element '{http://purl.org/dc/elements/1.1/}creat

In [154]:
print root.findall('{http://purl.org/dc/elements/1.1/}relation')

[]


In [151]:
dc = 'http://purl.org/dc/elements/1.1/'
print root.find('{http://purl.org/dc/elements/1.1}relation')

None


In [97]:
print(ET.tostring(root, encoding='utf8').decode('utf8'))

<?xml version='1.0' encoding='utf8'?>
<ns0:OAI-PMH xmlns:dc="http://purl.org/dc/elements/1.1/" xmlns:ns0="http://www.openarchives.org/OAI/2.0/" xmlns:ns2="http://www.openarchives.org/OAI/2.0/oai_dc/" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" xsi:schemaLocation="http://www.openarchives.org/OAI/2.0/ http://www.openarchives.org/OAI/2.0/OAI-PMH.xsd">
  <ns0:responseDate>2018-11-19T15:33:56Z</ns0:responseDate>
  <ns0:request metadataPrefix="oai_dc" set="user-ecfunded" verb="ListRecords">https://zenodo.org/oai2d</ns0:request>
  <ns0:ListRecords>
    <ns0:record>
      <ns0:header>
        <ns0:identifier>oai:zenodo.org:166408</ns0:identifier>
        <ns0:datestamp>2017-09-08T08:42:37Z</ns0:datestamp>
        <ns0:setSpec>openaire</ns0:setSpec>
        <ns0:setSpec>user-ecfunded</ns0:setSpec>
        <ns0:setSpec>user-fp7-bmc</ns0:setSpec>
      </ns0:header>
      <ns0:metadata>
        <ns2:dc xsi:schemaLocation="http://www.openarchives.org/OAI/2.0/oai_dc/ http://www.openarchiv

In [140]:
#listRecords, record, metadata, dc, relation
#root[2][0][1][0][11].text
#for index in range(0, 90):
    #print(root[2][index][1][0][11].text)
print(root[2][0][1][0][11].text)
print(root[2][1][1][0][11].text)
    #print(root[2][index][1][0][7].text)

info:eu-repo/grantAgreement/EC/FP7/619166/
བསམ་ཡས་ central Tibet, inscribed pillar.


In [133]:
for relation in root.iter('dc%3Arelation'):
    print(relation.attrib)

In [144]:
for record in root[2].iter('relation'):
    print record.attrib